# Primeritat i factorització

###  Artur Travesa

#### (versió 2024-07)

# Capítol 10: Construcció certificada de claus RSA

## 10.0. Introducció

En el capítol 3 hem après a construir nombres naturals primers certificables de mida prefixada. Però, per exemple, per a la construcció de claus per al criptosistema RSA, cal que, a més a més, els primers satisfacin altres condicions extres.

L'objectiu d'aquest capítol és aprendre a construir nombres primers de mida (en bits) prefixada, de certificar que ho són, de primers, i fer-ho de manera que se satisfacin algunes condicions extres que detallarem més avall, a fi que s'assemblin més als especificats als estàndards per a les claus RSA per a certificats digitals (cf. [DS-S, A.1.1]). 

I com a exemple, construirem una parella de nombres primers de $2048$ bits cadascun de manera que el seu producte sigui un nombre natural de $4096$ bits i tals que se satisfacin algunes condicions extres necessàries per a poder formar part d'una clau RSA de $4096$ bits per a signatures digitals.

<b>Observació</b>. El sol fet de donar-los a conèixer, ja els invalida per a ser-ho de debò, de part d'una clau; però poden servir com a exemple.

### 10.0.0. Funcions que aprofitarem de capítols anteriors

#### 10.0.0.0. Tests de primeritat i certificats de composició

In [ ]:
def SolovayStrassenTest(nn,ff):
    if nn==1:
        return false
    if nn in [2,3,5,7]:
        return true
    if is_even(nn):
        return false
    if ff<1:
        return 'Cal fer alguna prova.'
    f=0
    n2=(nn-1)//2
    while f<ff:
        g=ZZ.random_element(2,nn-1)
        x=Mod(g,nn)^n2
        if x==1 or x==nn-1:
            y=Mod(kronecker(g,nn),nn)
            if y!=x:
                return false
        else:
            return false
        f=f+1
    return 'Indeterminat'


In [ ]:
def MillerRabinTest(nn,ff):
    if nn==1:
        return false
    if nn in [2,3,5,7]:
        return true
    if is_even(nn):
        return false
    if ff<1:
        return 'Cal fer alguna prova.'
    v=0
    m=nn-1
    while is_even(m):
        v=v+1
        m=m//2
    f=0
    while f<ff:
        g=ZZ.random_element(2,nn-1)
        x=Mod(g,nn)^m
        if x!=1 and x!=nn-1:
            k=1
            x=x^2
            while (x!=nn-1 and k<v-1):
                x=x^2
                k=k+1
            if k>=v-1 and x!=nn-1:
                return false
        f=f+1
    return 'Indeterminat'


In [ ]:
def SolovayStrassenCert(nn,ff):
    if nn==1:
        return [nn,false,1]
    if nn==2 or nn==3:
        return [nn,true,nn-1,[nn-1]]
    if nn==5:
        return [nn,true,2,[2]]
    if nn==7:
        return [nn,true,3,[2,3]]
    if is_even(nn):
        return [nn,false,2]
    if ff<1:
        return 'Cal fer alguna prova.'
    f=0
    n2=(nn-1)//2
    while f<ff:
        g=ZZ.random_element(2,nn-1)
        x=Mod(g,nn)^n2
        if x ==1 or x==nn-1:
            y=Mod(kronecker(g,nn),nn)
            if y!=x:
                return [nn,false,g]
        else:
            return [nn,false,g]
        f=f+1
    return 'Indeterminat'


In [ ]:
def MillerRabinCert(nn,ff):
    if nn==1:
        return [nn,false,1]
    if nn==2 or nn==3:
        return [nn,true,nn-1,[nn-1]]
    if nn==5:
        return [nn,true,2,[2]]
    if nn==7:
        return [nn,true,3,[2,3]]
    if is_even(nn):
        return [nn,false,2]
    if ff<1:
        return 'Cal fer alguna prova.'
    v=0
    m=nn-1
    while is_even(m):
        v=v+1
        m=m//2
    f=0
    while f<ff:
        g=ZZ.random_element(2,nn-1)
        x=Mod(g,nn)^m
        if x!=1 and x!=nn-1:
            k=1
            x=x^2
            while (x!=nn-1 and k<v-1):
                x=x^2
                k=k+1
            if k>=v-1 and x!=nn-1:
                return [nn,false,g]
        f=f+1
    return 'Indeterminat'


#### 10.0.0.1. Certificats de primeritat

In [ ]:
def Certifica(pp,fppmu,ff):
    if pp==1:
        return [pp,false,1]
    if pp==2 or pp==3:
        return [pp,true,pp-1,[pp-1]]
    if is_even(pp):
        return [pp,false,2]
    if ff<1:
        return ["Cal fer alguna prova."]
    if len(fppmu)==0:
        lta1=factor(pp-1)
        lta=[lta1[i][0] for i in range(len(lta1))]
    else:
        lta=sorted(fppmu)
    l=len(lta)
    f=0
    while f<ff:
        g=ZZ.random_element(2,pp-2)
        if (s:=Mod(g,pp)^((pp-1)//2))==pp-1:
            i=1
            while i<= l-1 and Mod(g,pp)^((pp-1)//lta[i])!=1:
                i=i+1
            if i==l:
                return [pp,true,g,lta]
        else:
            if s!=1:
                return [pp,false,g]
        f=f+1
    return [pp,'Indeterminat']


In [ ]:
def Pocklington(pp,tt,ff):
    if not pp in ZZ or pp<1:
        return ['Cal que el nombre P sigui enter positiiu.']
    if pp==1:
        return [pp,false,1]
    if pp==2 or pp==3:
        return [pp,true,pp-1,[pp-1]]
    if is_even(pp):
        return [pp,false,2]
    if ff<1:
        return 'Cal fer alguna prova.'
# Comprovació que la llista tt és de divisors de pp-1, i càlcul de U;
# però no que són primers.
    if false in [(r in ZZ and r>1) for r in tt]:
        return 'La llista T no és de nombres enters >1.'
# Si 2 no pertany a la llista tt, li afegim (per a millora del càlcul)
    t=tt
    if not (2 in t):
        t=[2]+t
    x=prod(t)
    q,r=divmod(pp-1,x)
    if r:
        return 'La llista T no és correcta.'
    d=gcd(q,x)
    while d>1:
        q=q//d
        d=gcd(q,x)
    uu=q
    q=uu^2
    if q==pp:
        return [pp,false,uu]
    if q>pp:
        return 'U és massa gran.'
    t=sorted(t)
# Si hem arribat aquí, és que P, T, F i U són correctes (excepte,
# potser, que alguns elements de T no siguin primers).
    l=len(t)
    f=0
    while f<ff:
        g=ZZ.random_element(2,pp-2)
        if (s:=Mod(g,pp)^((pp-1)//2))==pp-1:
            i=1
            while i<= l-1 and gcd((s:=Mod(g,pp)^((pp-1)//t[i]))-1,pp)==1 and s^t[i]==1:
                i=i+1
            if i==l:
                return [pp,true,g,t]
        else:
            if s!=1:
                return [pp,false,g]
        f=f+1
    return [pp,'Indeterminat']    


## 10.1. Restriccions per a les claus RSA per a signatura digital

D'acord amb els estàndards per a les claus RSA per a signatures digitals (cf. [DS-S, A.1.1]), les longituds dels mòduls $n$ de les claus, en bits, han de ser nombres parells, posem $2L$, i com a mínim de $2048$ bits (o sigui, $2L\ge2048$). 

A més a més, el mòdul $n$ és el producte de dos nombres naturals primers diferents, $p$, $q$, tals que 

$p-1$ és divisible per un nombre primer $p_1$, 

$p+1$ és divisible per un nombre primer $p_2$, 

$q-1$ és divisible per un nombre primer $q_1$, 

$q+1$ és divisible per un nombre primer $q_2$, 

i de manera que les longituds (en bits) dels primers $p_i$, $q_i$, satisfacin les restriccions següents, en cas que siguin certificables (o amb la darrera condició menys restrictiva si els primers no se certifiquen):

<table width=90%>
    <tbody>
    <tr>
        <td style="text-align: center;">$len(n)=2L$</td> 
        <td style="text-align: center;">len($p_i$),
            <br>len($q_i$)</td>
        <td style="text-align: center;">len($p_1$)+len($p_2$),
            <br>len($q_1$)+len($q_2$)
            <br>(si els primers se certifiquen)</td> 
        <td style="text-align: center;">len($p_1$)+len($p_2$),
            <br>len($q_1$)+len($q_2$)
            <br>(si els primers no se certifiquen)</td>
    </tr>
    <tr>
        <td style="text-align: center;">$2048\le 2L<3072$</td>
        <td style="text-align: center;">$>140$ bits</td>
        <td style="text-align: center;">$\le 494$ bits</td>
        <td style="text-align: center;">$\le 1007$ bits</td>
    </tr>
    <tr>
        <td style="text-align: center;">$3072\le 2L<4096$</td>
        <td style="text-align: center;">$>170$ bits</td>
        <td style="text-align: center;">$\le 750$ bits</td>
        <td style="text-align: center;">$\le 1518$ bits</td>
    </tr>
    <tr>
        <td style="text-align: center;">$4096\le 2L$</td>
        <td style="text-align: center;">$>200$ bits</td>
        <td style="text-align: center;">$\le 1005$ bits</td>
        <td style="text-align: center;">$\le 2030$ bits</td>
    </tr>
    </tbody>
</table>

A més a més, 

cadascun dels primers $p$ i $q$ ha de ser de $L$ bits; de fet, $p$ i $q$ han de pertànyer a l'interval $2^{L-1}\sqrt{2}\le p,q\le 2^L-1$, i

el valor absolut, $|p-q|$, de la seva diferència ha de ser com a mínim $2^{L-100}$.

<b>Observació</b>. Encara que l'estàndard no ho especifica, les restriccions anteriors sobre la divisibilitat per primers $p_i$, $q_i$, 
són per a (intentar) evitar els mètodes de factorització $p-1$ de Pollard, i $p+1$, de Williams; la restricció sobre el valor absolut de la diferència és per a (intentar) evitar el mètode de factorització de Fermat, i la restricció sobre la mida dels primers $p_i$, $q_i$, i encara més, sobre l'interval al qual han de pertànyer, permet assegurar que el seu producte, $n$, és de $2L$ bits.

## 10.2. Primers de 112 bits

L'objectiu final és construir un parell de nombres primers $p$, $q$, de $2048$ bits cadascun, de la forma 
$$
p=2 m_p p_0 p_1 + 1,
\qquad
q=2m_q q_0 q_1 + 1, 
$$
de manera que $p_0$, $p_1$, $q_0$, $q_1$, siguin primers, que $p_1$, $q_1$ siguin de més de $200$ bits cadascun (o sigui, $p_1, q_1>2^{199}$), que $p<(p_0 p_1)^2$, $q<(q_0 q_1)^2$, i que $m_p$ sigui divisible per un nombre primer $p_2$ de més de $200$ bits tal que $len(p_1)+len(p_2)\le 1005$ bits, i que $m_q$ sigui divisible per un nombre primer $q_2$ de més de $200$ bits tal que $len(q_1)+len(q_2)\le 1005$ bits, i que se satisfacin les altres restriccions per a les longituds i la diferència entre $p$ i $q$.

Com que hi ha una restricció per a la diferència entre $p$ i $q$, serà convenient construir-los simultàniament, imposant aquesta condició en la construcció. 

D'altra banda, la construcció dels nombres $m_p$ i $m_q$ ha de ser tal que es garanteixi la condició que $p+1$ i $q+1$ siguin divisibles per primers $p_2$, $q_2$, respectivament, de la longitud predeterminada.


### 10.2.0. Construcció d'una primera llista de nombres primers 

Es tracta de construir una llista, que anomenarem lp112, de $32$ nombres primers de $112$ bits i certificar-los, però sense emmagatzemar, ni escriure, els certificats. (En farem servir $24$, d'aquests nombres, però en tenim més per si algun presentés problemes.)

<b>Observació</b>. Els nombres d'aquesta llista són prou petits perquè puguin ésser certificats fàcilment amb la funció Certifica; per això no emmagatzemarem els certificats.

Per a construir aquesta llista, definirem una funció Primer112( )
que calculi un nombre primer d'aquesta mida a partir d'una cercar a l'atzar entre els nombres senars de $112$ bits. Un cop feta la tria, li passarem el test de Solovay-Strassen, de manera que si el nombre triat és compost, no passarà el test i en triarem un altre. Això ho farem successivament un màxim de, posem, $500$ vegades. Un cop en tinguem un que passi el test (que, per tant, deu ser primer), el certificarem com a primer i el retornarem. Si no és primer o si hem arribat al final sense trobar-ne cap en el nombre màxim fixat de tries, retornarem $0$.

Després, aplicarem aquesta funció per a fer una llista de $32$ nombres.

In [ ]:
def Primer112():
    fita=500
    n=0
    while not SolovayStrassenCert((q:=(2*ZZ.random_element(2^110,2^111)+1)),25)[1] and n<fita:
        n=n+1
    if n<fita and Certifica(q,[],50)[1]:
        return q
    return 0


In [ ]:
lp112=[Primer112() for i in range(32)]

Encara que no cal, podem veure'n certificats (que fem de nou); notem que, com que no coneixem prou primers que divideixin p-1, és més útil la funció Certifica que la funció Pocklington.

In [ ]:
[Certifica(lp112[i],[],50) for i in range(len(lp112))]

## 10.3. Primers de 480 bits

Notem que el producte de quatre nombres de $112$ bits és un nombre de (aproximadament) $448$ bits. Sigui $np1$ el producte de quatre d'aquests nombres de $lp112$; concretament, prendrem el primer, el quadrat del segon i el tercer; o sigui, farem 
$$
np1:=lp112[0]\cdot lp112[1]^2\cdot lp112[2].
$$
Anàlogament, considerarem 
$$
np2:=lp112[4]\cdot lp112[5]^2\cdot lp112[6],
$$
$$
nq1:=lp112[8]\cdot lp112[9]^2\cdot lp112[10],
$$
$$
nq2:=lp112[12]\cdot lp112[13]^2\cdot lp112[14].
$$
Farem servir aquests nombres per a la construcció dels primers $p_1$, $p_2$, $q_1$ i $q_2$.

I també considerarem 
$$
np00:=lp112[16]\cdot lp112[17]^2\cdot lp112[18],
$$
$$
nq00:=lp112[20]\cdot lp112[21]^2\cdot lp112[22],
$$
$$
np01:=lp112[24]\cdot lp112[25]^2\cdot lp112[26],
$$
$$
nq01:=lp112[28]\cdot lp112[29]^2\cdot lp112[30],
$$
nombres que farem servir com a auxiliars per a la construcció de $p_0$ i de $q_0$.

In [ ]:
[np1,np2,nq1,nq2,np00,nq00,np01,nq01]=[lp112[4*i]*lp112[4*i+1]^2*lp112[4*i+2] for i in range(8)]

Tot i que no cal, mirem-nos-els.

In [ ]:
[np1,np2,nq1,nq2,np00,nq00,np01,nq01]

Òbviament, aquests nombres no són ni de $480$ bits, ni (probablement) primers; però a partir d'ells podem calcular fàcilment nombres primers de $480$ bits de la manera següent. Ens fixem en $np1$; per als altres, es fa el mateix.

Per a tot nombre natural $kp1$, el nombre $p_1:=2*kp1*np1+1$ és senar; i el seu nombre de bits depèn d'un interval on es pot triar $kp1$; de fet, si volem que $p_1$ sigui de $480$ bits, cal que
$$
2^{479}\le p_1=2*kp1*np1+1< 2^{480}
$$
i, per tant, hem de prendre $kp1$ com un nombre enter de l'interval 
$$
\dfrac{2^{479}-1}{2\cdot np1} \le kp1 < \dfrac{2^{480}-1}{2\cdot np1}.
$$
Notem que la longitud de l'interval és 
$$
\dfrac{2^{480}-1}{2\cdot np1}-\dfrac{2^{479}-1}{2\cdot np1}=
\dfrac{2^{480}-2^{479}}{2\cdot np1}=\dfrac{2^{478}}{np1}\ge 
\dfrac{2^{478}}{2^{4\cdot112}}=2^{30},
$$
de manera que hi ha molts valors de $kp1$ per poder triar a l'atzar.

I, anàlogament, per a les parelles $(kp2,p_2)$, $(kq1,q_1)$, i $(kq2,q_2)$.

Ara, la tria dels valors de $kp1$, $kp2$, $kq1$, $kq2$ en els intervals adequats produeix nombres $p_1$, $p_2$, $q_1$ i $q_2$ de la quantitat desitjada de bits; però (segurament) no són primers!

Calculem les fites per als intervals.

In [ ]:
infkp1=ceil((2^479-1)/(2*np1))
supkp1=floor((2^480-1)/(2*np1))
infkp2=ceil((2^479-1)/(2*np2))
supkp2=floor((2^480-1)/(2*np2))
infkq1=ceil((2^479-1)/(2*nq1))
supkq1=floor((2^480-1)/(2*nq1))
infkq2=ceil((2^479-1)/(2*nq2))
supkq2=floor((2^480-1)/(2*nq2))

Triem valors aleatoris.

In [ ]:
kp1=ZZ.random_element(infkp1,supkp1)
kp2=ZZ.random_element(infkp2,supkp2)
kq1=ZZ.random_element(infkq1,supkq1)
kq2=ZZ.random_element(infkq2,supkq2)

Encara que no cal, els podem veure.

In [ ]:
kp1, kp2, kq1, kq2

Amb aquests valors de $kp1$, $kp2$, $kq1$ i $kq2$, definim nombres $p_1$, $p_2$, $q_1$, $q_2$, als quals aplicarem el test de primeritat de Solovay-Strassen a fi de comprovar que no són primers, o de tenir gran certesa que ho són. 

I repetirem la tria a l'atzar dels valors $kp1$, $kp2$, $kq1$ i $kq2$, fins que el test no detecti que el nombre és compost. En aquest cas, podrem certificar-lo com a primer amb el certificat de Pocklington, perquè els productes de primers que hem pres per a $np1$, $np2$, $nq1$ i $nq2$ són més grans que l'arrel quadrada del primer corresponent que volem certificar (de fet, amb el primer del qual hem considerat el quadrat i un els altres dos, ja en tenim prou). 

Això produirà, doncs, els nombres primers $p_1$, $p_2$, $q_1$ i $q_2$ que volem, amb certificats (que, si no cal, podem obviar).

Per a aquesta tasca, definim una funció Primer480(ltanp) que automatitzi aquest procés i es pugui aplicar de manera senzilla a cadascun dels casos. Aquí, ltanp és (una part significativa de) la llista de primers que divideixen $p-1=2\cdot k\cdot np$; i la funció retorna p, el valor k i un certificat de primeritat de p.

<b>Observació</b>. La funció està adaptada a la construcció que fem dels nombres np i no és general; per exemple, construeix el nombre np tal com ho hem fet a partir de la llista, però no cap altre nombre construït a partir dels seus elements.

In [ ]:
def Primer480(ltanp):
    np=ltanp[0]*ltanp[1]^2*ltanp[2]
    infkp=ceil((2^479-1)/(2*np))
    supkp=floor((2^480-1)/(2*np))
    kp=ZZ.random_element(infkp,supkp)
    p=2*kp*np+1
    fita=1000
    while fita >0 and SolovayStrassenTest(p,50)==false:
        kp=ZZ.random_element(infkp,supkp)
        p=2*kp*np+1
        fita=fita-1
    if fita==0:
        return 0, 'Cal tornar-hi!'
    else:
        cert=Pocklington(p,ltanp[0:2],50)
    return [p,kp,cert]

### 10.3.1. Construcció dels nombres primers p1, p2, q1 i q2, de 480 bits

Apliquem la funció per a construir $p_1$, $p_2$, $q_1$ i $q_2$, amb els seus respectius certificats.

In [ ]:
[p1,kp1,certp1]=Primer480(lp112[0:3])

In [ ]:
[q1,kq1,certq1]=Primer480(lp112[4:7])

In [ ]:
[p2,kp2,certp2]=Primer480(lp112[8:11])

In [ ]:
[q2,kq2,certq2]=Primer480(lp112[12:15])

Tot i que no cal, els podem veure, així com també que se satisfan les restriccions de la seva mida.

In [ ]:
p1,p2,q1,q2

In [ ]:
2^479<p1<2^480

In [ ]:
2^479<p2<2^480

In [ ]:
2^479<q1<2^480

In [ ]:
2^479<q2<2^480

## 10.4. Primers de 1024 bits

### 10.4.0. Construcció dels primers p0 i q0

Anàlogament a la construcció dels nombres primers $p_1$, $p_2$, $q_1$ i $q_2$ anteriors, podem construir nombres primers $p'_0$, $p'_1$, $q'_0$, $q'_1$, també de $480$ bits, a fi de construir $p_0:=2\cdot kp_0\cdot p'_0\cdot p'_1$, i $q_0:=2\cdot kq_0\cdot q'_0\cdot q'_1$, de $1024$ bits a partir del càlcul dels valors $kp_0$ i $kq_0$, a l'atzar, com més amunt (en l'interval adequat).

Repetim, doncs, el procediment. Només cal aplicar la funció Primer480( ) a la llista adequada en cada cas.

In [ ]:
[pp0,kpp0,certpp0]=Primer480(lp112[16:19])

In [ ]:
[pq0,kpq0,certpq0]=Primer480(lp112[20:23])

In [ ]:
[pp1,kpp1,certpp1]=Primer480(lp112[24:27])

In [ ]:
[pq1,kpq1,certpq1]=Primer480(lp112[28:31])

Per a la construcció de $p_0$, $q_0$, serà útil repetir la funció Primer480 però per a $1024$ bits i a partir de dos primers de $480$ bits.

In [ ]:
def Primer1024(ltanp):
    np=ltanp[0]*ltanp[1]
    infkp=ceil((2^1023-1)/(2*np))
    supkp=floor((2^1024-1)/(2*np))
    kp=ZZ.random_element(infkp,supkp)
    p=2*kp*np+1
    fita=2000
    while fita >0 and SolovayStrassenTest(p,50)==false:
        kp=ZZ.random_element(infkp,supkp)
        p=2*kp*np+1
        fita=fita-1
    if fita==0:
        return 0, 'Cal tornar-hi!'
    else:
        cert=Pocklington(p,ltanp,50)
    return [p,kp,cert]

In [ ]:
[p0,kp0,certp0]=Primer1024([pp0,pp1])

In [ ]:
[q0,kq0,certq0]=Primer1024([pq0,pq1])

## 10.5. Primers de 2048 bits

Notem que fins ara hem construït nombres primers prou grans i de manera que si escrivim $p=2m_p\cdot p_0\cdot p_1$, i anàlogament per a $q$, els nombres $p-1$ i $q-1$ són divisibles per un primer de $480$ bits.

Resta trobar els valors de $m_p$ i $m_q$ de manera que $p$ i $q$ siguin primers, de la mida volguda, per als quals se satisfaci la restricció sobre la seva diferència, i tals que $p+1$ i $q+1$ siguin divisibles per algun primer de $480$ bits (els $p_2$, $q_2$ que hem calculat més amunt).

Considerem els nombres enters $y_p$, $y_q$, dels intervals $1\le y_p\le p_0p_1-1$, $1\le y_q\le q_0q_1-1$, inversos de $p_0p_1\pmod{p_2}$ i $q_0q_1\pmod{q_2}$, respectivament; és a dir, tals que $y_p p_0p_1\equiv 1\pmod{p_2}$ i $y_q q_0q_1\equiv 1\pmod{q_2}$.

Ara es tracta de trobar nombres naturals $t_p$ i $t_q$ adequats, de manera que per a $m_p:=t_p p_2-y_p$, $m_q:=t_q q_2-y_q$, els nombres $p:=2m_pp_0p_1+1$, $q:=2m_qq_0q_1+1$, satisfacin les condicions volgudes.

Notem que per a tots els nombres de la forma $m_p:=t_p p_2-y_p$, tenim que
$$
p+1=2m_pp_0p_1+2=2(t_pp_2-y_p)p_0p_1+2\equiv -2y_pp_0p_1+2\equiv 0\pmod{p_2};
$$
i anàlogament per a $q+1$:
$$
q+1=2m_qq_0q_1+2=2(t_qq_2-y_q)q_0q_1+2\equiv -2y_qq_0q_1+2\equiv 0\pmod{q_2};
$$
és a dir, $p+1$ i $q+1$ són divisibles per $p_2$, $q_2$, respectivament. 

Així, només cal construir els valors $t_p$ i $t_q$ de manera que se satisfacin les altres condicions (mida dels $p$ i $q$, valor absolut de la diferència, i que siguin primers).

### 10.5.0. Construcció de yp i yq

In [ ]:
[yp,yq]=[Integer(Mod(p0*p1,p2)^(-1)),Integer(Mod(q0*q1,q2)^(-1))]

In [ ]:
[yp,yq]

### 10.5.1. Construcció de p

De manera similar com hem calculat valors $kp1$, $kp2$, $kq1$, $kq2$, i altres, ara calcularem els valors $t_p$ i $t_q$.

I a fi de poder calcular els nombres $p$ i $q$ d'acord amb la restricció que el valor absolut de la diferència sigui més gran que $2^{2048-100}=2^{1948}$, primerament calcularem $p$ i, després podrem calcular $q$ en tenir en compte el valor de $p$.

Per comoditat de lectura (i també de càlcul), posarem $a:=2^{2047}\sqrt{2}$ i $b:=2^{2048}$.

Notem que volem que se satisfacin les condicions sobre la mida de $p$ i de $q$:
$$
a< p=2(t_p p_2-y_p)𝑝_0𝑝_1+1 <b,
$$
$$
a< q=2(t_q q_2-y_q)q_0q_1+1 <b;
$$
per tant, ha de ser
$$
\dfrac{a-1}{2𝑝_0𝑝_1}+y_p< t_p p_2 <
\dfrac{b-1}{2𝑝_0𝑝_1}+y_p;
$$
o sigui,
$$
\dfrac{a-1+2𝑝_0𝑝_1y_p}{2𝑝_0𝑝_1}< t_p p_2 <
\dfrac{b-1+2𝑝_0𝑝_1y_p}{2𝑝_0𝑝_1};
$$
és a dir,
$$
\dfrac{a-1+2𝑝_0𝑝_1y_p}{2𝑝_0𝑝_1p_2}< t_p <
\dfrac{b-1+2𝑝_0𝑝_1y_p}{2𝑝_0𝑝_1p_2}.
$$
I, anàlogament, 
$$
\dfrac{a-1+2q_0q_1y_q}{2q_0q_1q_2}< t_q <
\dfrac{b-1+2q_0q_1y_q}{2q_0q_1q_2}.
$$

<b>Observació</b>. Més avall canviarem aquestes fites per a $t_q$.

Ara, en tenir en compte les mides dels primers $p_0$, $p_1$, $p_2$, notem que això permet triar $t_p$ en un interval de longitud
$$
\dfrac{b-1+2𝑝_0𝑝_1y_p}{2𝑝_0𝑝_1p_2}-
\dfrac{a-1+2𝑝_0𝑝_1y_p}{2𝑝_0𝑝_1p_2}=
\dfrac{b-a}{2𝑝_0𝑝_1p_2}=
\dfrac{2^{2046}(2-\sqrt{2})}{𝑝_0𝑝_1p_2}>
2^{2046-1024-480-480}(2-\sqrt{2})
=2^{62}(2-\sqrt{2})>2^{61}.
$$

És a dir, podem triar $t_p$ a l'atzar en un interval prou gran i esperar que alguna tria proporcioni un nombre primer de la mida volguda.


Comencem per definir un parell de nombres, sq($=a$), i sq2($=r$) per a comparar i calcular les fites dels intervals.

In [ ]:
sq=2^2047*sqrt(2)

In [ ]:
sq2=(2^2048+sq)/2

Escrivim les fites de l'interval per al càlcul de $p$.

In [ ]:
inftp=ceil((sq-1+2*p0*p1*yp)/(2*p0*p1*p2))
suptp=floor((2^2048-1+2*p0*p1*yp)/(2*p0*p1*p2))

Calculem, successivament, $t_p$, $m_p$, i $p$.

In [ ]:
tp=ZZ.random_element(inftp,suptp)

In [ ]:
mp=tp*p2-yp

In [ ]:
p=2*mp*p0*p1+1

Tot i que no cal, els podem veure.

In [ ]:
mp

In [ ]:
p

In [ ]:
SolovayStrassenTest(p,50)

Com era d'esperar, $p$ no és primer; cal repetir el càlcul de $p$; ho automatitzem.

In [ ]:
fita=2000

In [ ]:
while SolovayStrassenTest(p,50)==false and fita>0:
    tp=ZZ.random_element(inftp,suptp)
    mp=tp*p2-yp
    p=2*mp*p0*p1+1
    fita=fita-1
if fita==0:
    primerp=0
    print('Cal tornar-hi!')
else:
    primerp=[p,Pocklington(p,[p0],100)]
    

Tot i que no cal, el podem veure, amb un certificat.

In [ ]:
primerp

I (òbviament) se satisfan les condicions volgudes per a $p$.

In [ ]:
(p-1)%p1

In [ ]:
(p+1)%p2

In [ ]:
sq<p<2^2048

### 10.5.2. Construcció de q

Per a la tria del valor de $q$, cal triar $t_q$ de manera similar a $t_p$. Però ara, podem recalcular l'interval a fi que se satisfaci la propietat que $|p-q|\ge 2^{1948}$.

Notem que podem bipartir l'interval $[a:=2^{2047}\sqrt{2}, b:=2^{2048}]$ pel seu punt mitjà, 
$$
r:=\dfrac{a+b}{2}=\dfrac{2^{2047}\sqrt{2}+2^{2048}}{2}=2^{2046}(2+\sqrt{2}),
$$
mirar en quina de les dues meitats hi ha $p$, i imposar que $q$ estigui a l'altra (i prou separat de $p$).

Més concretament, volem imposar que se satisfaci que si $a<p<r$, llavors sigui $r+2^{1948}<q<b$, i que si $r<p<b$, llavors sigui $a<q<r-2^{1948}$.

Per tant, només cal adaptar adequadament els intervals de cerca de $t_q$.

<b>Observació</b>. És (molt) probable que una tria a l'atzar de $t_p$ i $t_q$ en l'interval predit ja faci que se satisfaci la condició sobre el valor absolut de la diferència entre $p$ i $q$. I en cas (molt poc probable) que no se satisfés, podríem tornar a calcular un dels primers (o tots dos). Amb el procediment que hem descrit, ens assegurem que això succeeixi. A canvi, però, perdem la propietat que tots dos nombres siguin "prou" aleatoris, perquè imposem que estiguin en meitats complementàries de l'interval $[a,b]$.


Així, les noves fites són:

En el cas que $a<p<r$, cal que 
$$
\dfrac{a+2^{1948}-1+2q_0q_1y_q}{2q_0q_1q_2}< t_q <
\dfrac{b-1+2q_0q_1y_q}{2q_0q_1q_2};
$$
i en el cas que $r<p<b$, cal que 
$$
\dfrac{a-1+2q_0q_1y_q}{2q_0q_1q_2}< t_q <
\dfrac{2^{2046}(\sqrt{2}+1)-1+2q_0q_1y_q-2^{1948}}{2q_0q_1q_2};
$$


Calculem-les.

In [ ]:
if p<sq2:
    inftq=ceil((sq+2^1948-1+2*q0*q1*yq)/(2*q0*q1*q2))
    suptq=floor((2^2048-1+2*q0*q1*yq)/(2*q0*q1*q2))
else:
    inftq=ceil((sq-1+2*q0*q1*yq)/(2*q0*q1*q2))
    suptq=floor((2^2048-1+2*q0*q1*yq-2^1948)/(2*q0*q1*q2))

Encara que no cal, les podem veure.

In [ ]:
inftq,suptq

Calculem, successivament, $t_q$, $m_q$, i $q$.

In [ ]:
tq=ZZ.random_element(inftq,suptq)

In [ ]:
mq=tq*q2-yq

In [ ]:
q=2*mq*q0*q1+1

Encara que no cal, els podem veure.

In [ ]:
tq

In [ ]:
mq

In [ ]:
q

In [ ]:
SolovayStrassenTest(q,50)

Com era d'esperar, $q$ no és primer; cal repetir el càlcul de $q$; ho automatitzem.

In [ ]:
fita=2000

In [ ]:
while SolovayStrassenTest(q,50)==false and fita>0:
    tq=ZZ.random_element(inftq,suptq)
    mq=tq*q2-yq
    q=2*mq*q0*q1+1
    fita=fita-1
if fita==0:
    primerq=0
    print('Cal tornar-hi!')
else:
    primerq=[q,Pocklington(q,[q0],100)]
    

In [ ]:
primerq

I se satisfan les condicions volgudes per a $q$.

In [ ]:
q=primerq[0]

In [ ]:
q

In [ ]:
(q-1)%q1

In [ ]:
(q+1)%q2

In [ ]:
sq<q<2^2048

In [ ]:
abs(p-q)>2^1948

In [ ]:
2^4095<p*q<2^4096

In [ ]:
n=p*q

In [ ]:
n

## 10.6. Els valors obtinguts per a una possible clau

In [ ]:
p

In [ ]:
q

In [ ]:
p0

In [ ]:
p1

In [ ]:
p2

In [ ]:
q0

In [ ]:
q1

In [ ]:
q2

In [ ]:
n

Per a completar una clau, calen els exponents públic, e, i privat, d, de manera que $de \equiv 1\pmod{lcm(p-1,q-1)}$. I es recomana triar $d$ a l'atzar, i prèviament al càlcul de $p$ i $q$; óbviament, obviarem aquest pas previ i construirem $d$ i $e$ ara.

Notem que $d$ i $e$ han de ser, en particular, senars.

In [ ]:
m=lcm(p-1,q-1)

In [ ]:
m

In [ ]:
d=2*ZZ.random_element(2,(m-2)//2)+1

In [ ]:
d

In [ ]:
e=Mod(d,m)^(-1)

In [ ]:
e

Escrivim les claus:

In [ ]:
ClauPublicaRSA4096=[n,e]

In [ ]:
ClauPrivadaRSA4096=[n,d]

In [ ]:
ClauPublicaRSA4096

In [ ]:
ClauPrivadaRSA4096

Notem que, efectivament, $n$ és de 4096 bits.

In [ ]:
2^4095<n<2^4096

## Fi del capítol 10